# VacationPy
---

## Starter Code to Import Libraries and Load the Weather and Coordinates Data

In [51]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import time
import json
from scipy.stats import linregress
import scipy.stats as st
from scipy.stats import pearsonr
from scipy import stats
import holoviews as hv
import geoviews as gv
from citipy import citipy
import hvplot.pandas
from pprint import pprint

# Import the OpenWeatherMap API key
from api_keys import weather_api_key
from api_keys import geoapify_key

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

In [20]:
# Load the CSV file created in Part 1 into a Pandas DataFrame
city_data_df = pd.read_csv("output_data/cities.csv")

# Display sample data
city_data_df.head()

City_ID         City      Lat       Lng  MaxTemp  Humidity  Cloudiness  \
0        0       xining  36.6167  101.7667    -8.80        90         100   
1        1        tumut -35.3000  148.2167    19.63        95         100   
2        2  east london -33.0153   27.9116    23.52        83           0   
3        3    grytviken -54.2811  -36.5092     8.38        64          64   
4        4   georgetown   5.4112  100.3354    28.97        78          20   

   WindSpeed Country        Date  
0       0.74      CN  1707157951  
1       1.31      AU  1707157952  
2       2.06      ZA  1707157952  
3       5.63      GS  1707157952  
4       3.09      MY  1707157717

---

### Step 1: Create a map that displays a point for every city in the `city_data_df` DataFrame. The size of the point should be the humidity in each city.

In [21]:
#%%capture --no-display
#Configure the map plot_1
map_plot_1 = city_data_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "EsriNatGeo",
    frame_width = 800,
    frame_height = 600,
    size = "Humidity",
    scale = 1,
    color = "City"
)

# Display the map plot
map_plot_1


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Humidity)

### Step 2: Narrow down the `city_data_df` DataFrame to find your ideal weather condition

In [22]:
# Narrow down cities that fit criteria and drop any results with null values
ideal_city_df = city_data_df[city_data_df['MaxTemp'] >= 26 & (city_data_df['MaxTemp']<32) ]
#ideal_city_df

# Drop any rows with null values
ideal_city_df.dropna(inplace=True)

# Display sample data
print(ideal_city_df)

     City_ID         City      Lat       Lng  MaxTemp  Humidity  Cloudiness  \
1          1        tumut -35.3000  148.2167    19.63        95         100   
2          2  east london -33.0153   27.9116    23.52        83           0   
3          3    grytviken -54.2811  -36.5092     8.38        64          64   
4          4   georgetown   5.4112  100.3354    28.97        78          20   
6          6     waitangi -43.9535 -176.5597    17.68        93          98   
..       ...          ...      ...       ...      ...       ...         ...   
569      569  mikhaylovsk  45.1283   42.0256     3.21       100         100   
570      570   las tablas   7.7667  -80.2833    35.10        99          73   
571      571    lexington  37.9887  -84.4777    13.47        34           0   
572      572        dahab  28.5010   34.5134    16.30        35           0   
573      573     kalmunai   7.4167   81.8167    24.90        83          56   

     WindSpeed Country        Date  
1         1.31

### Step 3: Create a new DataFrame called `hotel_df`.

In [23]:
# Use the Pandas copy function to create DataFrame called hotel_df to store the city, country, coordinates, and humidity
# Create a copy of the DataFrame with four columns
hotel_df = ideal_city_df.copy()[['City', 'Country', 'Lat', 'Lng','Humidity']]

# Add an empty column, "Hotel Name," to the DataFrame so you can store the hotel found using the Geoapify API
hotel_df['HotelName'] = ''

# Display sample data
print(hotel_df)

hotel_df.columns

            City Country      Lat       Lng  Humidity HotelName
1          tumut      AU -35.3000  148.2167        95          
2    east london      ZA -33.0153   27.9116        83          
3      grytviken      GS -54.2811  -36.5092        64          
4     georgetown      MY   5.4112  100.3354        78          
6       waitangi      NZ -43.9535 -176.5597        93          
..           ...     ...      ...       ...       ...       ...
569  mikhaylovsk      RU  45.1283   42.0256       100          
570   las tablas      PA   7.7667  -80.2833        99          
571    lexington      US  37.9887  -84.4777        34          
572        dahab      EG  28.5010   34.5134        35          
573     kalmunai      LK   7.4167   81.8167        83          

[451 rows x 6 columns]


Index(['City', 'Country', 'Lat', 'Lng', 'Humidity', 'HotelName'], dtype='object')

In [24]:
# Extract the lat and Long column and assign them to variables to avoid 'Lat','Lng' not defined error
latitude= hotel_df['Lat']
longitude = hotel_df['Lng']

print(latitude, longitude)

1     -35.3000
2     -33.0153
3     -54.2811
4       5.4112
6     -43.9535
        ...   
569    45.1283
570     7.7667
571    37.9887
572    28.5010
573     7.4167
Name: Lat, Length: 451, dtype: float64 1      148.2167
2       27.9116
3      -36.5092
4      100.3354
6     -176.5597
         ...   
569     42.0256
570    -80.2833
571    -84.4777
572     34.5134
573     81.8167
Name: Lng, Length: 451, dtype: float64


### Step 4: For each city, use the Geoapify API to find the first hotel located within 10,000 metres of your coordinates.

In [33]:
# Set parameters to search for a hotel
radius = 10000
limit = 5
filters = f"circle:{longitude},{latitude},{radius}"
bias = f"proximity:{longitude},{latitude}"

#Set parameters dictionary
params = {
    "filter":filters,
    "limit":limit,
    "bias":bias,
    "apiKey":geoapify_key    
}

# Set base URL
base_url = "https://api.geoapify.com/v2/places"

# Print a message to follow up the hotel search
print("Starting hotel search")

# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    latitude = hotel_df.loc[index,'Lat']
    longitude = hotel_df.loc[index,'Lng']  
    
# Add filter and bias parameters with the current city's latitude and longitude to the params dictionary
params["filter"] = f"circle:{longitude},{latitude},{radius}"
params["bias"] = f"proximity:{longitude},{latitude}"
params["categories"] = f"accommodation.hotel"   

# Make API request using the params dictionaty
hotel = requests.get(base_url, params=params)
    
# Convert the API response to JSON format
hotel = hotel.json()
print(hotel)


Starting hotel search
{'type': 'FeatureCollection', 'features': [{'type': 'Feature', 'properties': {'name': 'Saji new food', 'country': 'Sri Lanka', 'country_code': 'lk', 'state': 'Eastern Province', 'county': 'Ampara District', 'city': 'Karaitivu', 'hamlet': 'Sainthamaruthu', 'postcode': '32280', 'street': 'Colombo-Ratnapura-Wellawaya-Batticaloa Road', 'lon': 81.830522, 'lat': 7.4072879, 'formatted': 'Saji new food, Colombo-Ratnapura-Wellawaya-Batticaloa Road, Karaitivu 32280, Sri Lanka', 'address_line1': 'Saji new food', 'address_line2': 'Colombo-Ratnapura-Wellawaya-Batticaloa Road, Karaitivu 32280, Sri Lanka', 'categories': ['accommodation', 'accommodation.hotel'], 'details': ['details'], 'datasource': {'sourcename': 'openstreetmap', 'attribution': '© OpenStreetMap contributors', 'license': 'Open Database Licence', 'url': 'https://www.openstreetmap.org/copyright', 'raw': {'osm_id': 6397685785, 'name:en': 'Saji new food', 'tourism': 'hotel', 'osm_type': 'n'}}, 'distance': 1847, 'plac

In [39]:
# Grab the first hotel from the results and store the name in the hotel_df DataFrame
    
# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    latitude = hotel_df.loc[index, 'Lat']
    longitude = hotel_df.loc[index, 'Lng']

    # Add filter and bias parameters with the current city's latitude and longitude to the params dictionary
    params["filter"] = f"circle:{longitude},{latitude},{radius}"
    params["bias"] = f"proximity:{longitude},{latitude}"
    params["categories"] = f"accommodation.hotel"

    # Make an API request using the params dictionary
    hotel = requests.get(base_url, params=params)

    # Convert the API response to JSON format
    hotel = hotel.json()
    pprint(hotel)

{'features': [{'geometry': {'coordinates': [148.2226596982952,
                                            -35.30227205429335],
                            'type': 'Point'},
               'properties': {'address_line1': 'Star Hotel',
                              'address_line2': 'Russell Street, Tumut NSW '
                                               '2720, Australia',
                              'categories': ['accommodation',
                                             'accommodation.hotel',
                                             'building',
                                             'building.accommodation'],
                              'city': 'Tumut',
                              'country': 'Australia',
                              'country_code': 'au',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                             'license': 

{'features': [{'geometry': {'coordinates': [27.913796199999997,
                                            -33.0185051995307],
                            'type': 'Point'},
               'properties': {'address_line1': 'Inverleith Terrace',
                              'address_line2': 'Quigney, East London, 5201, '
                                               'South Africa',
                              'categories': ['accommodation',
                                             'accommodation.hotel'],
                              'city': 'East London',
                              'country': 'South Africa',
                              'country_code': 'za',
                              'county': 'Buffalo City Metropolitan '
                                        'Municipality',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                           

{'features': [], 'type': 'FeatureCollection'}
{'features': [{'geometry': {'coordinates': [100.33484049999998,
                                            5.41232329947872],
                            'type': 'Point'},
               'properties': {'address_line1': 'Page 63 hostel',
                              'address_line2': 'Beach Street, 10300 George '
                                               'Town, Penang, Malaysia',
                              'categories': ['accommodation',
                                             'accommodation.hotel'],
                              'city': 'George Town',
                              'country': 'Malaysia',
                              'country_code': 'my',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                             'license': 'Open Database Licence',
                                         

{'features': [{'geometry': {'coordinates': [-176.56071569999997,
                                            -43.95094920078155],
                            'type': 'Point'},
               'properties': {'address_line1': 'Hotel Chathams',
                              'address_line2': '1 Waitangi Wharf Owenga Road, '
                                               'Waitangi 8942, New Zealand',
                              'categories': ['accommodation',
                                             'accommodation.hotel'],
                              'city': 'Waitangi',
                              'country': 'New Zealand',
                              'country_code': 'nz',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                             'license': 'Open Database Licence',
                                             'raw': {'addr:city': 'Waitangi',

{'features': [], 'type': 'FeatureCollection'}
{'features': [{'geometry': {'coordinates': [-25.429007381480076,
                                            37.71638475461738],
                            'type': 'Point'},
               'properties': {'address_line1': "Vinha d'Areia Beach Hotel",
                              'address_line2': 'Rua da Marina, 9680-146 Vila '
                                               'Franca do Campo, Portugal',
                              'categories': ['accommodation',
                                             'accommodation.hotel',
                                             'building',
                                             'building.accommodation'],
                              'city': 'Vila Franca do Campo',
                              'country': 'Portugal',
                              'country_code': 'pt',
                              'datasource': {'attribution': '© OpenStreetMap '
                                           

...

{'features': [{'geometry': {'coordinates': [42.064193499999995,
                                            45.13673010045461],
                            'type': 'Point'},
               'properties': {'address_line1': 'Усадьба',
                              'address_line2': 'посёлок СНИИСХ 18 к2, '
                                               'Mikhaylovsk, Stavropol Krai, '
                                               'Russia, 356241',
                              'categories': ['accommodation',
                                             'accommodation.hotel'],
                              'city': 'Mikhaylovsk',
                              'country': 'Russia',
                              'country_code': 'ru',
                              'county': 'Shpakovsky District',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                             'l

{'features': [{'geometry': {'coordinates': [-80.27866928217752,
                                            7.770029796721229],
                            'type': 'Point'},
               'properties': {'address_line1': 'Hotel Don Jesus',
                              'address_line2': 'Calle Ramón Mora, Las Tablas, '
                                               'Los Santos, Panama',
                              'categories': ['accommodation',
                                             'accommodation.hotel',
                                             'building',
                                             'building.accommodation'],
                              'city': 'Las Tablas',
                              'country': 'Panama',
                              'country_code': 'pa',
                              'county': 'Distrito Las Tablas',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                       

{'features': [{'geometry': {'coordinates': [-84.49517932368333,
                                            37.984046608506425],
                            'type': 'Point'},
               'properties': {'address_line1': 'Extended Stay America',
                              'address_line2': '3575 Tates Creek Road, '
                                               'Lexington, KY 40517, United '
                                               'States of America',
                              'categories': ['accommodation',
                                             'accommodation.hotel',
                                             'building',
                                             'building.accommodation'],
                              'city': 'Lexington',
                              'country': 'United States',
                              'country_code': 'us',
                              'county': 'Fayette County',
                              'datasource': {'attributio

{'features': [{'geometry': {'coordinates': [34.5160827, 28.500880399890864],
                            'type': 'Point'},
               'properties': {'address_line1': 'Lighthouse Hotel',
                              'address_line2': 'Othman Ibn Affan Street, '
                                               'Masbat, Dahab, 45214, Egypt',
                              'categories': ['accommodation',
                                             'accommodation.hotel'],
                              'city': 'Dahab',
                              'country': 'Egypt',
                              'country_code': 'eg',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                             'license': 'Open Database Licence',
                                             'raw': {'air_conditioning': 'yes',
                                                     'name': 

{'features': [{'geometry': {'coordinates': [81.83052199999999,
                                            7.407287899396153],
                            'type': 'Point'},
               'properties': {'address_line1': 'Saji new food',
                              'address_line2': 'Colombo-Ratnapura-Wellawaya-Batticaloa '
                                               'Road, Karaitivu 32280, Sri '
                                               'Lanka',
                              'categories': ['accommodation',
                                             'accommodation.hotel'],
                              'city': 'Karaitivu',
                              'country': 'Sri Lanka',
                              'country_code': 'lk',
                              'county': 'Ampara District',
                              'datasource': {'attribution': '© OpenStreetMap '
                                                            'contributors',
                                       

In [37]:
# If and else added to Try/Except statement code code block to run through entire hotel list  
#https://bootcampspot.instructure.com/courses/4981/external_tools/313

    # Check if any hotels were found in the response
    if len(hotel["features"]) > 0:
        # Grab the first hotel from the results and store the name in the hotel_df DataFrame
        try:
            hotel_name = hotel["features"][0]["properties"]["name"]
            hotel_df.loc[index, "HotelName"] = hotel_name
        except KeyError:
            hotel_df.loc[index, "HotelName"] = "Name not available"
    else:
        # If no hotel is found, set the hotel name as "No hotel found"
        hotel_df.loc[index, "HotelName"] = "No hotel found"

    # Log the search results
    print(f"{hotel_df.loc[index, 'City']} - nearest hotel: {hotel_df.loc[index, 'HotelName']}")



tumut - nearest hotel: Star Hotel
east london - nearest hotel: Name not available
grytviken - nearest hotel: No hotel found
georgetown - nearest hotel: Page 63 hostel
waitangi - nearest hotel: Hotel Chathams
taichung - nearest hotel: 塔木德一中館
albany - nearest hotel: No hotel found
vila franca do campo - nearest hotel: Vinha d'Areia Beach Hotel
edinburgh of the seven seas - nearest hotel: No hotel found
port augusta - nearest hotel: Hotel Commonwealth
malango - nearest hotel: Madarana
avarua - nearest hotel: Paradise Inn
san luis de la loma - nearest hotel: No hotel found
adamstown - nearest hotel: No hotel found
ushuaia - nearest hotel: Apart Hotel Aires del Beagle
inhambane - nearest hotel: Hotel de Inhambane
nova sintra - nearest hotel: Residência Ka Dencho
port saint john's - nearest hotel: Outback Inn
hilo - nearest hotel: Dolphin Bay Hotel
port shepstone - nearest hotel: The Spot Backpackers'
papatowai - nearest hotel: No hotel found
geiro - nearest hotel: No hotel found
la passe - 

bonthe - nearest hotel: No hotel found
pacific grove - nearest hotel: Pacific Grove Inn
dongola - nearest hotel: Lord
along - nearest hotel: Hotel Toshi Palace
kerikeri - nearest hotel: Avalon Resort
badou - nearest hotel: Hôtel Billy Grâce
mount isa - nearest hotel: Ibis Styles
touros - nearest hotel: Pousada Atlântico
sinop - nearest hotel: No hotel found
eirunepe - nearest hotel: No hotel found
svetlyy - nearest hotel: Гостиница Спортивная
phumi veal sre - nearest hotel: Sweet Home Guesthouse
saint-leu - nearest hotel: Iloha Seaview Hôtel
bikenibeu village - nearest hotel: Otintaai Hotel
cuyo - nearest hotel: Feroland Hotel
whangarei - nearest hotel: Grand Hotel
oyem - nearest hotel: Hôtel comfort
nelson bay - nearest hotel: Name not available
antofagasta - nearest hotel: Hotel Colón
lagos - nearest hotel: No hotel found
kamalpur - nearest hotel: No hotel found
whitby - nearest hotel: Resolution Hotel
moyale - nearest hotel: Paul’s guest house
liberal - nearest hotel: Days Inn
chiro

badiyah - nearest hotel: Al Areen Hotel Apartments
fortaleza - nearest hotel: Hotel Catedral
saint-philippe - nearest hotel: Le Baril
east wenatchee bench - nearest hotel: Name not available
sijunjung - nearest hotel: Hotel Bukik Gadang
lospalos - nearest hotel: Hotel Roberto Carlos
st. paul - nearest hotel: Crowne Plaza
oamaru - nearest hotel: Brydone Hotel Oamaru
shasta lake - nearest hotel: Fairfield Inn & Suites Redding
muynoq - nearest hotel: Lala
alpena - nearest hotel: Ramada of Alpena
batie - nearest hotel: No hotel found
copiapo - nearest hotel: Hotel Diego de Almeida
unai - nearest hotel: Hotel Fazenda Curva do Rio
borcka - nearest hotel: Name not available
nakonde - nearest hotel: Zwangendaba Executive Lodge
alice springs - nearest hotel: Aurora Alice Springs
illizi - nearest hotel: بوناقة
ghanzi - nearest hotel: Ghanzi farmhouse
manismata - nearest hotel: No hotel found
carutapera - nearest hotel: No hotel found
borba - nearest hotel: No hotel found
saint-pierre - nearest h

In [38]:
# Display sample data
hotel_df

City Country      Lat       Lng  Humidity              HotelName  \
1          tumut      AU -35.3000  148.2167        95             Star Hotel   
2    east london      ZA -33.0153   27.9116        83     Name not available   
3      grytviken      GS -54.2811  -36.5092        64         No hotel found   
4     georgetown      MY   5.4112  100.3354        78         Page 63 hostel   
6       waitangi      NZ -43.9535 -176.5597        93         Hotel Chathams   
..           ...     ...      ...       ...       ...                    ...   
569  mikhaylovsk      RU  45.1283   42.0256       100                Усадьба   
570   las tablas      PA   7.7667  -80.2833        99        Hotel Don Jesus   
571    lexington      US  37.9887  -84.4777        34  Extended Stay America   
572        dahab      EG  28.5010   34.5134        35       Lighthouse Hotel   
573     kalmunai      LK   7.4167   81.8167        83          Saji new food   

         Hotel Name  
1               NaN  
2               NaN  
3               NaN  
4               NaN  
6               NaN  
..              ...  
569             NaN  
570             NaN  
571             NaN  
572             NaN  
573  No hotel found  

[451 rows x 7 columns]

### Step 5: Add the hotel name and the country as additional information in the hover message for each city in the map.

In [50]:
#%%capture --no-display

# Configure the map plot
#https://bootcampspot.instructure.com/courses/4981/external_tools/313 for coding hover columns

import hvplot.pandas

map_plot_2 = city_data_df.hvplot.points(
    "Lng",
    "Lat",
    geo=True,
    tiles="EsriNatGeo",
    frame_width=800,
    frame_height=600,
    size="Humidity",
    scale=1,
    color="City",
    hover_data=["HotelName", "Country"]
)

# Display the map plot
map_plot_2.opts(width=800, height=600)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Humidity)